# Data Preparation

Я нашел три датасета на kaggle по классификации фейков. Они все на английском, поэтому для поддержки русскуязычных статей будем использовать специально обученную для перевода новостей модель wmt19-ru-en. 

Выбранные датасеты:
* https://www.kaggle.com/c/fake-news/data
* https://www.kaggle.com/c/fakenewskdd2020/data
* https://www.kaggle.com/c/classifying-the-fake-news/data

In [95]:
import pandas as pd

df1_train = pd.read_csv('./data1/train.csv')

In [96]:
df1_train

id                                              title  \
0          0  House Dem Aide: We Didn’t Even See Comey’s Let...   
1          1  FLYNN: Hillary Clinton, Big Woman on Campus - ...   
2          2                  Why the Truth Might Get You Fired   
3          3  15 Civilians Killed In Single US Airstrike Hav...   
4          4  Iranian woman jailed for fictional unpublished...   
...      ...                                                ...   
20795  20795  Rapper T.I.: Trump a ’Poster Child For White S...   
20796  20796  N.F.L. Playoffs: Schedule, Matchups and Odds -...   
20797  20797  Macy’s Is Said to Receive Takeover Approach by...   
20798  20798  NATO, Russia To Hold Parallel Exercises In Bal...   
20799  20799                          What Keeps the F-35 Alive   

                                          author  \
0                                  Darrell Lucus   
1                                Daniel J. Flynn   
2                             Consortiumnews.com   
3                                Jessica Purkiss   
4                                 Howard Portnoy   
...                                          ...   
20795                              Jerome Hudson   
20796                           Benjamin Hoffman   
20797  Michael J. de la Merced and Rachel Abrams   
20798                                Alex Ansary   
20799                              David Swanson   

                                                    text  label  
0      House Dem Aide: We Didn’t Even See Comey’s Let...      1  
1      Ever get the feeling your life circles the rou...      0  
2      Why the Truth Might Get You Fired October 29, ...      1  
3      Videos 15 Civilians Killed In Single US Airstr...      1  
4      Print \nAn Iranian woman has been sentenced to...      1  
...                                                  ...    ...  
20795  Rapper T. I. unloaded on black celebrities who...      0  
20796  When the Green Bay Packers lost to the Washing...      0  
20797  The Macy’s of today grew from the union of sev...      0  
20798  NATO, Russia To Hold Parallel Exercises In Bal...      1  
20799    David Swanson is an author, activist, journa...      1  

[20800 rows x 5 columns]

In [97]:
df1_train['text'] = df1_train.apply(lambda x: str(x.title) + '. ' + str(x.text), axis=1)
df1_train = df1_train[['text', 'label']]

In [98]:
df2_train = pd.read_csv('./data2/train.csv', sep='\t')

In [99]:
# Битая строка
df2_train = df2_train.drop([1615])

In [100]:
df2_train

text label
0     Get the latest from TODAY Sign up for our news...     1
1     2d  Conan On The Funeral Trump Will Be Invited...     1
2     It’s safe to say that Instagram Stories has fa...     0
3     Much like a certain Amazon goddess with a lass...     0
4     At a time when the perfect outfit is just one ...     0
...                                                 ...   ...
4982  The storybook romance of WWE stars John Cena a...     0
4983  The actor told friends he’s responsible for en...     0
4984  Sarah Hyland is getting real.  The Modern Fami...     0
4985  Production has been suspended on the sixth and...     0
4986  A jury ruled against Bill Cosby in his sexual ...     0

[4986 rows x 2 columns]

In [104]:
df3_train = pd.read_csv('./data3/training.csv')

In [105]:
df3_train['text'] = df3_train.apply(lambda x: str(x.title) + '. ' + str(x.text), axis=1)
df3_train = df3_train[['text', 'label']]

In [106]:
all_data_train = df1_train.append(df2_train).append(df3_train)
all_data_train.to_csv('./train.csv', index=False)

# Training

In [1]:
#!pip install transformers
import transformers

In [2]:
from transformers import Trainer, TrainingArguments, LineByLineTextDataset

In [3]:
import pandas as pd

In [4]:
from datasets import Dataset

In [5]:
df = pd.read_csv('./train.csv')

In [6]:
df

text  label
0      House Dem Aide: We Didn’t Even See Comey’s Let...      1
1      FLYNN: Hillary Clinton, Big Woman on Campus - ...      0
2      Why the Truth Might Get You Fired.Why the Trut...      1
3      15 Civilians Killed In Single US Airstrike Hav...      1
4      Iranian woman jailed for fictional unpublished...      1
...                                                  ...    ...
57209  CHICAGO TRUMP RALLY CANCELLED: Radicals And BL...      1
57210  Trump supports completion of Dakota Access Pip...      0
57211   Obama Can’t Stop Winning As New Jobs Report S...      1
57212  Turkey bank regulator dismisses 'rumors' after...      0
57213  California mayors ask for governor's support f...      0

[57214 rows x 2 columns]

In [7]:
df['labels'] = df['label']

In [8]:
df = df[['text', 'labels']]

In [9]:
dataset = Dataset.from_pandas(df)

In [10]:
dataset

Dataset({
    features: ['text', 'labels'],
    num_rows: 57214
})

In [11]:
import torch
from transformers import AutoTokenizer, AutoModel, pipeline

model_name = 'distilbert-base-uncased-finetuned-sst-2-english'
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [12]:
def preprocess_function(examples):
    return tokenizer(examples["text"], padding=True, truncation=True)

In [13]:
dataset = dataset.map(preprocess_function, batched=True)

  0%|          | 0/58 [00:00<?, ?ba/s]

In [14]:
dataset_splitted = dataset.shuffle(1337).train_test_split(0.1)

In [15]:
dataset_splitted

DatasetDict({
    train: Dataset({
        features: ['text', 'labels', 'input_ids', 'attention_mask'],
        num_rows: 51492
    })
    test: Dataset({
        features: ['text', 'labels', 'input_ids', 'attention_mask'],
        num_rows: 5722
    })
})

In [16]:
from transformers import AutoModelForSequenceClassification

In [23]:
model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)

loading configuration file https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english/resolve/main/config.json from cache at C:\Users\andry/.cache\huggingface\transformers\4e60bb8efad3d4b7dc9969bf204947c185166a0a3cf37ddb6f481a876a3777b5.9f8326d0b7697c7fd57366cdde57032f46bc10e37ae81cb7eb564d66d23ec96b
Model config DistilBertConfig {
  "_name_or_path": "distilbert-base-uncased-finetuned-sst-2-english",
  "activation": "gelu",
  "architectures": [
    "DistilBertForSequenceClassification"
  ],
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "finetuning_task": "sst-2",
  "hidden_dim": 3072,
  "id2label": {
    "0": "NEGATIVE",
    "1": "POSITIVE"
  },
  "initializer_range": 0.02,
  "label2id": {
    "NEGATIVE": 0,
    "POSITIVE": 1
  },
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "output_past": true,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "ti

In [24]:
for name, param in model.named_parameters():
    if name in ['classifier.weight', 'classifier.bias']:
        param.requires_grad = True
    else:
        param.requires_grad = False

In [25]:
from sklearn.metrics import accuracy_score

def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    acc = accuracy_score(labels, preds)
    return {'accuracy': acc}

In [26]:
from transformers import Trainer, TrainingArguments

trainer = Trainer(
    model=model, train_dataset=dataset_splitted['train'], 
    eval_dataset=dataset_splitted['test'],
    compute_metrics=compute_metrics,
    args=TrainingArguments(
        load_best_model_at_end=True,
        output_dir="./my_saved_model", overwrite_output_dir=True,
        num_train_epochs=10, per_device_train_batch_size=64, 
        per_device_eval_batch_size=64,
        evaluation_strategy = "epoch",
        save_strategy = "epoch",
        save_steps=10_000, save_total_limit=2),
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
The following columns in the training set  don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 51492
  Num Epochs = 10
  Instantaneous batch size per device = 64
  Total train batch size (w. parallel, distributed & accumulation) = 64
  Gradient Accumulation steps = 1
  Total optimization steps = 8050


The following columns in the evaluation set  don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 5722
  Batch size = 64
Saving model checkpoint to ./my_saved_model\checkpoint-805
Configuration saved in ./my_saved_model\checkpoint-805\config.json
Model weights saved in ./my_saved_model\checkpoint-805\pytorch_model.bin
The following columns in the evaluation set  don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 5722
  Batch size = 64
Saving model checkpoint to ./my_saved_model\checkpoint-1610
Configuration saved in ./my_saved_model\checkpoint-1610\c

TrainOutput(global_step=8050, training_loss=0.6166538418598057, metrics={'train_runtime': 5516.6092, 'train_samples_per_second': 93.34, 'train_steps_per_second': 1.459, 'total_flos': 6.821011291594752e+16, 'train_loss': 0.6166538418598057, 'epoch': 10.0})